# Sistema de Compressão

$ \frac{d\dot{m}}{dt} = \frac{A_1}{L_C}(\phi (N(t), \dot{m})P_1 - P_P(t)) $

$ \frac{d P_P}{dt} = \frac{C_1^2}{\nu _P}(\dot{m}(t) - \alpha (t) K_\nu \sqrt{P_P - P_{out}}) $

$ \begin{matrix} A_1 & = & 2.6\centerdot 10^{-3} m² \\
\nu _P & = & 2.0 m³ \\
L_C & = & 2.0 m \\
K_\nu & = & \frac{0.38 kg}{(kPa)^{0.5}s} \\
P_1 & = & 4.5 MPa \\
P{out} & = & 5.0 MPa \end{matrix}
$

$ \frac{d\dot{m}}{dt} = \frac{2.6\centerdot 10^{-3}}{2.0}(1.5\centerdot 4.5 - P_P) $

$ \frac{d P_P}{dt} = \frac{479.029^2}{2.0}(\dot{m} - \alpha {0.38} \sqrt{P_P - 5.0}) $

#### Importações

In [69]:
import numpy as np
from scipy.optimize import fsolve
import casadi as ca
import plotly.graph_objects as go
import optuna
from plotly.subplots import make_subplots
import time
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader, TensorDataset

from libs.numSol import Simulation
from libs.Model import MyModel


#### Constantes e Variáveis Auxiliares

In [70]:
np.random.seed(42)
print(np.random.seed)

# Constantes
A1 = (2.6)*(10**-3)
Lc = 2
kv = 0.38
P1 = 4.5
P_out = 5
C = 479

timestep = 3 # Passos no passado para prever o próximo
epochs = 5000
nData = 3000 
nAlphas = 5 # Número de vezes que o Alfa irá mudar, considere o treino e os testes.
alphas = np.random.uniform(0.35,0.65, nAlphas+1) # Abertura da válvula
perturb = 1e-4
tempo = 300
dt = 0.1 # Tempo amostral

# Variáveis auxiliares
interval = [np.linspace(i * tempo, (i + 1) * tempo, nData) for i in range(nAlphas)]
interval_test = [np.linspace(i * 300, (i + 1) * 300, 3000) for i in range(nAlphas)]
massFlowrate = []
PlenumPressure = []
alpha_values = []
RNN_train = []
RNN_trainFut = []

<built-in function seed>


### Solução Numérica

##### Cálculo da Solução

In [71]:
# Crie uma instância da classe Simulation
sim = Simulation(A1, Lc, kv, P1, P_out, C, alphas, nAlphas, nData, perturb, tempo, dt)

# Execute a simulação
sim.run()

RNN_train = sim.RNN_train
RNN_trainFut = sim.RNN_trainFut
massFlowrate = sim.massFlowrate
PlenumPressure = sim.PlenumPressure
alpha_values = sim.alpha_values


##### Gráfico do Modelo

In [72]:
fig = make_subplots(rows=1, cols=3, subplot_titles=("Vazão vs Tempo", "Pressão vs Tempo", "Alpha vs Tempo"))

for i in range(0, nAlphas):
    # Vazão
    fig.add_trace(go.Scatter(x=interval[i], y=np.squeeze(massFlowrate[i]), mode='lines',
                             name='Vazão', legendgroup='massflow', showlegend=i == 0), row = 1, col = 1)
    # Pressão
    fig.add_trace(go.Scatter(x=interval[i], y=np.squeeze(PlenumPressure[i]), mode='lines',
                             name='Pressão', legendgroup='pressure', showlegend=i == 0), row = 1, col = 2)
    # Alphas
    fig.add_trace(go.Scatter(x=interval[i], y=np.squeeze(alpha_values[i]), mode='lines', 
                             name='Alphas', line=dict(dash='dash'), legendgroup='alpha', showlegend=i == 0), row = 1, col = 3)

# Atualiza layout
fig.update_layout(
    xaxis_title='Tempo',
    grid=dict(rows=1, columns=3),
    template='plotly',
    showlegend=False
)

# Mostra a figura
fig.show()


### Rede Neural

##### Dados de Treino

In [5]:
RNN_train = np.array(RNN_train)


X_train = []
y_train = []

for i in range(len(RNN_train) - timestep):
    X_train.append(RNN_train[i:i + timestep])  
    if i + timestep < len(RNN_train):           
        y_train.append(RNN_train[i + timestep, :2])  

X_train = torch.tensor(X_train, dtype=torch.float32)
y_train = torch.tensor(y_train, dtype=torch.float32)

x_min = X_train.amin(dim=(0, 1), keepdim=True)
x_max = X_train.amax(dim=(0, 1), keepdim=True)
print(x_min.shape)

y_train = y_train.unsqueeze(1)

torch.Size([1, 1, 3])


/tmp/ipykernel_6947/2752278696.py:12: UserWarning:

Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at ../torch/csrc/utils/tensor_new.cpp:278.)



##### Rede

##### Treinamento

In [6]:
# def objective(trial):
#     lr = trial.suggest_float('lr', 1e-6, 1e-3, log=True) 
#     units = trial.suggest_int('units', 32, 64)
#     batch_size = trial.suggest_int('batch_size', 16, 64) 
#     num_layers = trial.suggest_int('num_layers', 0, 5)  

#     model = create_model(lr, num_layers, units)

#     model.fit(X_train, y_train, epochs=250, batch_size=batch_size, verbose=0)

#     # Avaliação
#     loss = model.evaluate(X_train, y_train, verbose=0)
#     return loss

# study = optuna.create_study(direction='minimize')
# study.optimize(objective, n_trials=5)  # Ajuste o número de tentativas conforme necessário

# # Exibir os melhores hiperparâmetros
# print("Melhores hiperparâmetros: ", study.best_params)

In [64]:
model = MyModel(20, A1, Lc, kv, P1, P_out, C, dt, x_min, x_max)

train_dataset = TensorDataset(X_train, y_train)
train_loader_Adam = DataLoader(train_dataset, batch_size= 32 , shuffle=True)
train_loader_LBFGS = DataLoader(train_dataset)
Adam = optim.Adam
model.train_model(model, train_loader_Adam, 1e-5, 1000, Adam)

Epoch [1/1000], Loss: 5.152576567521736
Epoch [2/1000], Loss: 4.593245327345598
Epoch [3/1000], Loss: 4.092361021651897
Epoch [4/1000], Loss: 3.6388745109663843
Epoch [5/1000], Loss: 3.226245268321495
Epoch [6/1000], Loss: 2.8502782928918218
Epoch [7/1000], Loss: 2.506500685647098
Epoch [8/1000], Loss: 2.197526417815609
Epoch [9/1000], Loss: 1.9176770522396194
Epoch [10/1000], Loss: 1.664150025798822
Epoch [11/1000], Loss: 1.4333433322052458
Epoch [12/1000], Loss: 1.2232506076918481
Epoch [13/1000], Loss: 1.03119129323756
Epoch [14/1000], Loss: 0.8573918577704602
Epoch [15/1000], Loss: 0.7019585376736451
Epoch [16/1000], Loss: 0.565585873655673
Epoch [17/1000], Loss: 0.4479574923322145
Epoch [18/1000], Loss: 0.3479577129774256
Epoch [19/1000], Loss: 0.26434420281127574
Epoch [20/1000], Loss: 0.19585835387203485
Epoch [21/1000], Loss: 0.14086658958750747
Epoch [22/1000], Loss: 0.09789336176076804
Epoch [23/1000], Loss: 0.06574608406611979
Epoch [24/1000], Loss: 0.04296735066698113
Epoch

##### Dados de teste

In [65]:
massFlowrateTeste = []
PlenumPressureTeste = []
RNN_test = []
x_test = []
alpha_valuesTeste = []
aux1 = []
aux2 = []
alphasTeste = np.random.uniform(0.35,0.65, nAlphas) # Abertura da válvula
interval3 = np.linspace(0, 1500, 14997)
sim = Simulation(A1, Lc, kv, P1, P_out, C, alphasTeste, nAlphas, 3000, perturb, tempo, dt)

sim.run()

RNN_test = sim.RNN_train
massFlowrateTeste = sim.massFlowrate
PlenumPressureTeste = sim.PlenumPressure
alpha_valuesTeste = sim.alpha_values
time2 = sim.time

RNN_test = np.array(RNN_test)

for i in range(len(RNN_test) - 3):
    x_test.append(RNN_test[i:i + 3])

x_test = torch.tensor(x_test, dtype=torch.float32)

massFlowrateTeste = np.array(massFlowrateTeste)
PlenumPressureTeste = np.array(PlenumPressureTeste)
print(time2)

7.704607725143433


##### Gráfico Rede Neural

In [66]:
massFlowrate100, PlenumPressure100, timeteste = model.test_model(x_test, interval3, model)
print(f"Tempo total: {timeteste} segundos")

Tempo total: 5.5969460010528564 segundos


In [67]:
fig3 = make_subplots(rows=1, cols=3, subplot_titles=("Loss","Mass Flow Rate vs Time", "Plenum Pressure vs Time"))

fig3.add_trace(go.Scatter(x=interval3,y=np.squeeze(massFlowrate100),mode='lines',
                                line=dict(dash='solid')),row=1, col=2)
fig3.add_trace(go.Scatter(x=interval3,y=np.squeeze(PlenumPressure100),mode='lines',
                                line=dict(dash='solid')),row=1, col=3)



for i in range(nAlphas):
    # Modelo
    fig3.add_trace(go.Scatter(x=np.squeeze(interval_test[i]), y=np.squeeze(massFlowrateTeste[i]), mode='lines',name='Model Mass Flow Rate', line=dict(dash='dash', color='green')),
                  row=1, col=2)
    fig3.add_trace(go.Scatter(x=np.squeeze(interval_test[i]), y=np.squeeze(PlenumPressureTeste[i]), mode='lines', name= 'Model Plenum Pressure', line=dict(dash='dash', color='green')),
                  row=1, col=3)

fig3.update_layout(
    title='Resultados Rede Neural',
    xaxis_title='Time',
    yaxis_title='Value',
    template='plotly',
    showlegend=False
)
fig3.show()